<a href="https://colab.research.google.com/github/herosunly/100-Days-Of-ML-Code/blob/master/learn_word2vec.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data as tud
import torch.nn.parameter as Parameter

In [0]:
from collections import Counter
import sklearn
from sklearn.metrics.pairwise import cosine_similarity

import pandas as pd
import numpy as np
import scipy

import random
import math 

In [0]:
USE_CUDA = torch.cuda.is_available()
random.seed(1)
np.random.seed(1)
torch.manual_seed(1)

if USE_CUDA:
    torch.cuda.manual_seed(1)

In [0]:
#词向量相关的超参数
K = 100
C = 3
EMBEDDING_SIZE = 100
MAX_VOCAB_SIZE = 30000

#参数优化相关的参数
NUM_EPOCHS = 2
BATCH_SIZE = 128
LEARNING_RATE = 0.2 # the initial learning rate #学习率
    
LOG_FILE = "word-embedding.log"

In [0]:
with open("/content/gdrive/My Drive/Colab Notebooks/text8.train.txt", "r") as f: #读入文件
    text = f.read() #得到文本内容
    text = text.lower().split()
    vocab_dict = dict(Counter(text).most_common(MAX_VOCAB_SIZE - 1)) #两步得到单词字典表，key是单词，value是次数
    vocab_dict['<unk>'] = len(text) - sum(list(vocab_dict.values())) #把不常用的单词都编码为"<unk>"
    idx_to_word = list(vocab_dict.keys())
    word_to_idx = {word:ind for ind, word in enumerate(idx_to_word)}
    word_counts = np.array(list(vocab_dict.values()),dtype = np.float32)
    word_freqs = word_counts / sum(word_counts)
    
    VOCAB_SIZE = len(idx_to_word)
    

In [0]:
class WordEmbeddingDataset(tud.Dataset): #tud.Dataset父类
    def __init__(self, text, word_to_idx, idx_to_word, word_freqs, word_counts):
        ''' text: a list of words, all text from the training dataset
            word_to_idx: the dictionary from word to idx
            idx_to_word: idx to word mapping
            word_freq: the frequency of each word
            word_counts: the word counts
        '''
        super().__init__() #通过父类初始化模型，然后重写两个方法
        self.text_encoded = [word_to_idx.get(t, VOCAB_SIZE-1) for t in text]
        #字典 get() 函数返回指定键的值（第一个参数），如果值不在字典中返回默认值（第二个参数）。
        #取出text里每个单词word_to_idx字典里对应的索引,不在字典里返回"<unk>"的索引
        #"<unk>"的索引=29999，get括号里第二个参数应该写word_to_idx["<unk>"]，不应该写VOCAB_SIZE-1，虽然数值一样。
        
        self.text_encoded = torch.Tensor(self.text_encoded).long()
        #变成tensor类型，这里变成longtensor，也可以torch.LongTensor(self.text_encoded)
        
        self.word_to_idx = word_to_idx #保存数据
        self.idx_to_word = idx_to_word  #保存数据
        self.word_freqs = torch.Tensor(word_freqs) #保存数据
        self.word_counts = torch.Tensor(word_counts) #保存数据
        
    def __len__(self): #数据集有多少个item 
        #魔法函数__len__
        ''' 返回整个数据集（所有单词）的长度
        '''
        return len(self.text_encoded) #所有单词的总数
        
    def __getitem__(self, idx):
        #魔法函数__getitem__，这个函数跟普通函数不一样
        ''' 这个function返回以下数据用于训练
            - 中心词
            - 这个单词附近的(positive)单词
            - 随机采样的K个单词作为negative sample
        '''
        center_word = self.text_encoded[idx] 
        #print(center_word)
        #中心词索引
        #这里__getitem__函数是个迭代器，idx代表了所有的单词索引。
        
        pos_indices = list(range(idx-C, idx)) + list(range(idx+1, idx+C+1))
        #周围词索引的索引，比如idx=0时。pos_indices = [-3, -2, -1, 1, 2, 3] 
        #老师讲这里的时候，我不是特别明白
        
        pos_indices = [i%len(self.text_encoded) for i in pos_indices]
        #range(idx+1, idx+C+1)超出词汇总数时，需要特别处理，取余数
        
        pos_words = self.text_encoded[pos_indices]
        #周围词索引，就是希望出现的正例单词
        #print(pos_words)
        
        neg_words = torch.multinomial(self.word_freqs, K * pos_words.shape[0], True)
        #负例采样单词索引，torch.multinomial作用是对self.word_freqs做K * pos_words.shape[0]次取值，输出的是self.word_freqs对应的下标。
        #取样方式采用有放回的采样，并且self.word_freqs数值越大，取样概率越大。
        #每个正确的单词采样K个，pos_words.shape[0]是正确单词数量
        #print(neg_words)
        
        return center_word, pos_words, neg_words 

In [0]:

dataset = WordEmbeddingDataset(text, word_to_idx, idx_to_word, word_freqs, word_counts)
dataloader = tud.DataLoader(dataset, batch_size=BATCH_SIZE, shuffle=True, num_workers=4)  

In [0]:
class EmbeddingModel(nn.Module):
    def __init__(self, vocab_size, embed_size):
        ''' 初始化输入和输出embedding
        '''
        super().__init__()
        self.vocab_size = vocab_size 
        self.embed_size = embed_size
        
        
        #一般来说，横轴代表样本，纵轴代表特征
        self.in_embed = nn.Embedding(self.vocab_size, self.embed_size, sparse=False)
        self.out_embed = nn.Embedding(self.vocab_size, self.embed_size, sparse=False)
        
        initrange = 0.5 / self.embed_size # 后加的代码
        self.in_embed.weight.data.uniform_(-initrange, initrange) # 后加的代码
        self.out_embed.weight.data.uniform_(-initrange, initrange) # 后加的代码
        
    def forward(self, input_labels, pos_labels, neg_labels):
        '''
        input_labels: 中心词, [batch_size]
        pos_labels: 中心词周围 context window 出现过的单词 [batch_size * (window_size * 2)]
        neg_labelss: 中心词周围没有出现过的单词，从 negative sampling 得到 [batch_size, (window_size * 2 * K)]
        
        return: loss, [batch_size]
        '''
        
        batch_size = input_labels.size(0)
        
        input_embedding = self.in_embed(input_labels) # B * embed_size
        pos_embedding = self.out_embed(pos_labels) # B * (2*C) * embed_size
        neg_embedding = self.out_embed(neg_labels) # B * (2*C * K) * embed_size
      
        log_pos = torch.bmm(pos_embedding, input_embedding.unsqueeze(2)).squeeze(2) # B * (2*C)
        log_neg = torch.bmm(neg_embedding, -input_embedding.unsqueeze(2)).squeeze(2) # B * (2*C*K)
        log_pos = F.logsigmoid(log_pos).sum(1) # batch_size
        log_neg = F.logsigmoid(log_neg).sum(1) # batch_size
       
        loss = log_pos + log_neg
        
        return -loss
    
    def input_embeddings(self):
        return self.in_embed.weight.data.cpu().numpy()

In [0]:
model = EmbeddingModel(VOCAB_SIZE, EMBEDDING_SIZE)
if USE_CUDA:
    model = model.cuda()

In [0]:
def evaluate(filename, embedding_weights): 
    if filename.endswith(".csv"):
        data = pd.read_csv(filename, sep=",")
    else:
        data = pd.read_csv(filename, sep="\t")
    human_similarity = []
    model_similarity = []
    for i in data.iloc[:, 0:2].index:
        word1, word2 = data.iloc[i, 0], data.iloc[i, 1]
        if word1 not in word_to_idx or word2 not in word_to_idx:
            continue
        else:
            word1_idx, word2_idx = word_to_idx[word1], word_to_idx[word2]
            word1_embed, word2_embed = embedding_weights[[word1_idx]], embedding_weights[[word2_idx]]
            model_similarity.append(float(sklearn.metrics.pairwise.cosine_similarity(word1_embed, word2_embed)))
            human_similarity.append(float(data.iloc[i, 2]))

    return scipy.stats.spearmanr(human_similarity, model_similarity)# , model_similarity

def find_nearest(word):
    index = word_to_idx[word]
    embedding = embedding_weights[index]
    cos_dis = np.array([scipy.spatial.distance.cosine(e, embedding) for e in embedding_weights])
    return [idx_to_word[i] for i in cos_dis.argsort()[:10]]

In [0]:
optimizer = torch.optim.SGD(model.parameters(), lr=LEARNING_RATE)
for e in range(NUM_EPOCHS):
    for i, (input_labels, pos_labels, neg_labels) in enumerate(dataloader):
        
        
        # TODO
        input_labels = input_labels.long()
        pos_labels = pos_labels.long()
        neg_labels = neg_labels.long()
        if USE_CUDA:
            input_labels = input_labels.cuda()
            pos_labels = pos_labels.cuda()
            neg_labels = neg_labels.cuda()
            
        optimizer.zero_grad()
        loss = model(input_labels, pos_labels, neg_labels).mean()
        loss.backward()
        optimizer.step()

        if i % 100 == 0:
            with open(LOG_FILE, "a") as fout:
                fout.write("epoch: {}, iter: {}, loss: {}\n".format(e, i, loss.item()))
                print("epoch: {}, iter: {}, loss: {}".format(e, i, loss.item()))
            
        
        if i % 2000 == 0:
            embedding_weights = model.input_embeddings()
            sim_simlex = evaluate("/content/gdrive/My Drive/Colab Notebooks/simlex-999.txt", embedding_weights)
            sim_men = evaluate("/content/gdrive/My Drive/Colab Notebooks/men.txt", embedding_weights)
            sim_353 = evaluate("/content/gdrive/My Drive/Colab Notebooks/wordsim353.csv", embedding_weights)
            with open(LOG_FILE, "a") as fout:
                print("epoch: {}, iteration: {}, simlex-999: {}, men: {}, sim353: {}, nearest to monster: {}\n".format(
                    e, i, sim_simlex, sim_men, sim_353, find_nearest("monster")))
                fout.write("epoch: {}, iteration: {}, simlex-999: {}, men: {}, sim353: {}, nearest to monster: {}\n".format(
                    e, i, sim_simlex, sim_men, sim_353, find_nearest("monster")))
                
    embedding_weights = model.input_embeddings()
    np.save("embedding-{}".format(EMBEDDING_SIZE), embedding_weights)
    torch.save(model.state_dict(), "embedding-{}.th".format(EMBEDDING_SIZE))

epoch: 0, iter: 0, loss: 420.04718017578125
epoch: 0, iteration: 0, simlex-999: SpearmanrResult(correlation=-0.032228302671439925, pvalue=0.3200353279643488), men: SpearmanrResult(correlation=0.02834615147021892, pvalue=0.14987991989432836), sim353: SpearmanrResult(correlation=0.10738636496766309, pvalue=0.055365540785350144), nearest to monster: ['monster', 'disappointed', 'damage', 'sasquatch', 'consumers', 'pong', 'surgeon', 'fetched', 'randomness', 'riverside']

epoch: 0, iter: 100, loss: 191.6930389404297
epoch: 0, iter: 200, loss: 166.45928955078125
epoch: 0, iter: 300, loss: 146.63479614257812
epoch: 0, iter: 400, loss: 127.6275634765625
epoch: 0, iter: 500, loss: 109.23967742919922
epoch: 0, iter: 600, loss: 111.43701934814453
epoch: 0, iter: 700, loss: 86.08010864257812
epoch: 0, iter: 800, loss: 80.23326873779297
epoch: 0, iter: 900, loss: 72.62664794921875
epoch: 0, iter: 1000, loss: 71.55587005615234
epoch: 0, iter: 1100, loss: 72.99050903320312
epoch: 0, iter: 1200, loss: 

In [0]:
word_to_idx

{' ': 0,
 '<unk>': 27,
 'a': 3,
 'b': 19,
 'c': 12,
 'd': 11,
 'e': 1,
 'f': 15,
 'g': 17,
 'h': 9,
 'i': 5,
 'j': 25,
 'k': 22,
 'l': 10,
 'm': 14,
 'n': 4,
 'o': 6,
 'p': 16,
 'q': 26,
 'r': 7,
 's': 8,
 't': 2,
 'u': 13,
 'v': 21,
 'w': 18,
 'x': 24,
 'y': 20,
 'z': 23}

In [0]:
for e in range(NUM_EPOCHS):
    for i, (input_labels, pos_labels, neg_labels) in enumerate(dataloader):
      print(pos_labels)

[tensor([19804532,  8671236, 37212633, 72454596,  3255193, 61883385, 44219294,
        59418461, 31388925, 41398980, 14349771, 30655486, 44133993, 51330587,
         4092762,  9898158, 78736152, 11443232, 63583191, 44785047, 58000601,
        80587052, 64013400, 89633457, 74898958, 57337030, 54327147,  5407031,
        45026031, 58435128, 49618570, 32604250, 24636014, 85662741, 40971039,
        74543592, 60669675, 55146702, 69072079,  9147736, 87643151, 25346558,
        55599052, 41010194, 72423104, 88373049, 35449866, 87888570, 59388231,
        85295459, 65567012, 24415425, 32745572, 60238008, 75554179, 75235188,
        24601442, 23898090, 47398438, 38731614, 23485851, 20245741, 53616744,
        58182308, 54330553,   983778,  6817391, 16418125, 41700022, 75066569,
        60221141, 25067044, 15781175, 52837011, 74174740, 70457065, 80669787,
        15214380, 50390049, 89897464, 66347274, 88693385, 50830001, 49103869,
        70837179, 55894412, 26109982, 52176693, 79956077, 52819

KeyboardInterrupt: ignored

In [0]:
weights = torch.tensor([0, 10, 3, 0], dtype=torch.float) # create a tensor of weights
print(torch.multinomial(weights, 4))
print(torch.multinomial(weights, 4, replacement=True))

RuntimeError: ignored

In [0]:
weights = torch.tensor([0, 10, 3, 0], dtype=torch.float) # create a tensor of weights
print(torch.multinomial(weights, 2))
print(weights)
print(torch.multinomial(weights, 2, replacement=True))
print(weights)

tensor([1, 2])
tensor([ 0., 10.,  3.,  0.])
tensor([1, 1])
tensor([ 0., 10.,  3.,  0.])


In [0]:
weights

tensor([ 0., 10.,  3.,  0.])

In [0]:
a = torch.randn(4, 4)

In [0]:
a.sum()

tensor(-4.4892)

In [0]:
a.sum(1)

tensor([ 0.6853, -5.0143,  2.7131, -2.8733])